In [1]:
%load_ext nb_black

In [111]:
import boto3
import pandas as pd
import json
import re

In [112]:
client = boto3.client("cloudsearch")

In [113]:
domain_name = "cs-demo-2"
#domain_name = "test"

In [114]:
response = client.describe_domains(DomainNames=[domain_name])
doc_ep = response["DomainStatusList"][0]["DocService"]["Endpoint"]
search_ep = response["DomainStatusList"][0]["SearchService"]["Endpoint"]
print("doc_ep: ", doc_ep)
print("search_ep: ", search_ep)

doc_ep:  doc-cs-demo-2-zeqfvjtapfrywc5qahp6hd7fjm.ap-southeast-2.cloudsearch.amazonaws.com
search_ep:  search-cs-demo-2-zeqfvjtapfrywc5qahp6hd7fjm.ap-southeast-2.cloudsearch.amazonaws.com


In [115]:
doc_client = boto3.client("cloudsearchdomain", endpoint_url=f"https://{doc_ep}")

In [116]:
src_client = boto3.client("cloudsearchdomain", endpoint_url=f"https://{search_ep}")

In [117]:
file = "/Users/sridharkannam/Desktop/imdb_movies.txt"
with open(file, "r") as fp:
    imdb = json.load(fp)

In [118]:
print(len(imdb))
imdb[0]

5000


{'fields': {'directors': ['Joseph Gordon-Levitt'],
  'release_date': '2013-01-18T00:00:00Z',
  'rating': 7.4,
  'genres': ['Comedy', 'Drama'],
  'image_url': 'http://ia.media-imdb.com/images/M/MV5BMTQxNTc3NDM2MF5BMl5BanBnXkFtZTcwNzQ5NTQ3OQ@@._V1_SX400_.jpg',
  'plot': 'A New Jersey guy dedicated to his family, friends, and church, develops unrealistic expectations from watching porn and works to find happiness and intimacy with his potential true love.',
  'title': 'Don Jon',
  'rank': 1,
  'running_time_secs': 5400,
  'actors': ['Joseph Gordon-Levitt', 'Scarlett Johansson', 'Julianne Moore'],
  'year': 2013},
 'id': 'tt2229499',
 'type': 'add'}

In [119]:
movies_ll = [movie['fields'] for movie in imdb]
id_ll = [movie['id'] for movie in imdb]

print(len(movies_ll), len(id_ll))

5000 5000


In [134]:
movies_df = pd.DataFrame.from_records(movies_ll)
print(movies_df.shape)
movies_df['id'] = id_ll
movies_df['running_time_secs'] = movies_df['running_time_secs'].fillna(0)
movies_df['year'] = movies_df['year'].fillna(0)
movies_df['running_time_secs'] = movies_df['running_time_secs'].astype('int', errors='ignore')
movies_df['year'] = movies_df['year'].astype('int', errors='ignore')
movies_df['rating'] = movies_df['rating'].fillna(0)
movies_df = movies_df.fillna("MISSING")
movies_df['release_date'] = pd.to_datetime("20200101")
movies_df.head(2)

(5000, 12)


directors release_date  rating  \
0  [Joseph Gordon-Levitt]   2020-01-01     7.4   
1            [Ron Howard]   2020-01-01     8.3   

                              genres  \
0                    [Comedy, Drama]   
1  [Action, Biography, Drama, Sport]   

                                           image_url  \
0  http://ia.media-imdb.com/images/M/MV5BMTQxNTc3...   
1  http://ia.media-imdb.com/images/M/MV5BMTQyMDE0...   

                                                plot    title  rank  \
0  A New Jersey guy dedicated to his family, frie...  Don Jon     1   
1  A re-creation of the merciless 1970s rivalry b...     Rush     2   

   running_time_secs                                             actors  year  \
0               5400  [Joseph Gordon-Levitt, Scarlett Johansson, Jul...  2013   
1               7380      [Daniel Brühl, Chris Hemsworth, Olivia Wilde]  2013   

          id  
0  tt2229499  
1  tt1979320

In [135]:
movies_ll = movies_df.to_dict(orient="records")

In [136]:
movies = []
for movie in movies_ll:
    movies.append({"type": "add", "id": movie['id'], "fields": movie})

In [137]:
movies[0]

{'type': 'add',
 'id': 'tt2229499',
 'fields': {'directors': ['Joseph Gordon-Levitt'],
  'release_date': Timestamp('2020-01-01 00:00:00'),
  'rating': 7.4,
  'genres': ['Comedy', 'Drama'],
  'image_url': 'http://ia.media-imdb.com/images/M/MV5BMTQxNTc3NDM2MF5BMl5BanBnXkFtZTcwNzQ5NTQ3OQ@@._V1_SX400_.jpg',
  'plot': 'A New Jersey guy dedicated to his family, friends, and church, develops unrealistic expectations from watching porn and works to find happiness and intimacy with his potential true love.',
  'title': 'Don Jon',
  'rank': 1,
  'running_time_secs': 5400,
  'actors': ['Joseph Gordon-Levitt', 'Scarlett Johansson', 'Julianne Moore'],
  'year': 2013,
  'id': 'tt2229499'}}

In [138]:
movies_tmp = movies[61:]
movies_tmp = json.dumps(movies_tmp)


TypeError: Object of type Timestamp is not JSON serializable

In [139]:
response = src_client.upload_documents(documents=movies_tmp, contentType="application/json")
print(response["ResponseMetadata"]["HTTPStatusCode"])

ParamValidationError: Parameter validation failed:
Invalid type for parameter documents, value: [{'type': 'add', 'id': 'tt1272878', 'fields': {'directors': ['Baltasar Kormákur'], 'release_date': Timestamp('2020-01-01 00:00:00'), 'rating': 7.0, 'genres': ['Action', 'Comedy', 'Crime', 'Drama', 'Thriller'], 'image_url': 'http://ia.media-imdb.com/images/M/MV5BNTQ5MTgzNDg4OF5BMl5BanBnXkFtZTcwMjAyODEzOQ@@._V1_SX400_.jpg', 'plot': 'A DEA agent and a naval intelligence officer find themselves on the run after a botched attempt to infiltrate a drug cartel. While fleeing, they learn the secret of their shaky alliance: Neither knew that the other was an undercover agent.', 'title': '2 Guns', 'rank': 62, 'running_time_secs': 6540, 'actors': ['Denzel Washington', 'Mark Wahlberg', 'Paula Patton'], 'year': 2013, 'id': 'tt1272878'}}, {'type': 'add', 'id': 'tt1345836', 'fields': {'directors': ['Christopher Nolan'], 'release_date': Timestamp('2020-01-01 00:00:00'), 'rating': 8.6, 'genres': ['Action', 'C